In [1]:
from glob import glob
from os import listdir, symlink
import pandas

from collections import Counter

import MySQLdb
db = MySQLdb.connect(user='root', passwd='Nmmxhjgt1@', db='stimmenfryslan')

In [2]:
source = '/media/herbert/Herbert Kruitbos/Data Sets/Stimmen Fryslan 2018-06026/picture_game_recordings/'
destination = '/media/herbert/Herbert Kruitbos/Data Sets/Stimmen Fryslan 2018-06026/picture_game_recordings_for_voice_sauce/'

In [3]:
filenames = [
    filename
    for filename in glob(source + '*/*/*.wav')
    if any(
        filename.split('/')[-1].startswith('pg_' + word + '_')
        for word in {'ei', 'meeuw', 'maan', 'molen', 'mond', 'nagel', 'uil'}
    )
]

In [4]:
# for filename in filenames:
#     symlink(
#         '../picture_game_recordings/' + filename[len(source):],
#         destination + filename.split('/')[-1]
#     )

In [5]:
Counter(filename.split('/')[-3] for filename in filenames)
None

In [6]:
# left_over = pandas.read_csv('left_over/output.txt', sep='\t')
# left_over['A2c'] = [
#     x if type(x) == float else (
#         0 if x == '-' else float(x)
#     ) for x in left_over['A2c']
# ]

# left_over.drop(columns=[c for c in left_over.columns if c.startswith('Unnamed: ')], inplace=True)
# left_over = left_over.groupby(['Filename']).agg({
#     field: aggregations
#     for aggregations, fields in [
#         (['max'], ['t_ms']),
#         (['mean', 'std'],
#          ['H1c', 'H2c', 'H4c', 'A1c', 'A2c', 'A3c', 'H2Kc',
#           'H1H2c', 'H2H4c', 'H1A1c', 'H1A2c', 'H1A3c', 'H42Kc', 'H2KH5Kc', 'CPP',
#           'Energy', 'HNR05', 'HNR15', 'HNR25', 'HNR35', 'SHR', 'H1u', 'H2u',
#           'H4u', 'A1u', 'A2u', 'A3u', 'H2Ku', 'H5Ku', 'H1H2u', 'H2H4u', 'H1A1u',
#           'H1A2u', 'H1A3u', 'H42Ku', 'H2KH5Ku', 'strF0', 'sF0', 'pF0', 'shrF0',
#           'oF0', 'sF1', 'sF2', 'sF3', 'sF4', 'pF1', 'pF2', 'pF3', 'pF4', 'oF1',
#           'oF2', 'oF3', 'oF4', 'sB1', 'sB2', 'sB3', 'sB4', 'pB1', 'pB2', 'pB3',
#           'pB4', 'oB1', 'oB2', 'oB3', 'oB4', 'epoch', 'soe']),
#     ]
#     for field in fields
# })
# left_over.reset_index(drop=False, inplace=True)
# left_over['Filename'] = [filename[:-3] + 'wav' for filename in left_over['Filename']]

# parameters = pandas.concat([parameters, left_over])

In [7]:
sheets = []
for f in glob('voicesauce_output/*.txt') + ['left_over/output.txt']:
    parameters = pandas.read_csv(f, sep='\t')
    parameters['A2c'] = [
        x if type(x) == float else (
            0 if x == '-' else float(x)
        ) for x in parameters['A2c']
    ]
    parameters.drop(columns=[c for c in parameters.columns if c.startswith('Unnamed: ')], inplace=True)
    parameters = parameters.groupby(['Filename']).agg({
        field: aggregations
        for aggregations, fields in [
            (['max'], ['t_ms']),
            (['mean', 'std'],
             ['H1c', 'H2c', 'H4c', 'A1c', 'A2c', 'A3c', 'H2Kc',
              'H1H2c', 'H2H4c', 'H1A1c', 'H1A2c', 'H1A3c', 'H42Kc', 'H2KH5Kc', 'CPP',
              'Energy', 'HNR05', 'HNR15', 'HNR25', 'HNR35', 'SHR', 'H1u', 'H2u',
              'H4u', 'A1u', 'A2u', 'A3u', 'H2Ku', 'H5Ku', 'H1H2u', 'H2H4u', 'H1A1u',
              'H1A2u', 'H1A3u', 'H42Ku', 'H2KH5Ku', 'strF0', 'sF0', 'pF0', 'shrF0',
              'oF0', 'sF1', 'sF2', 'sF3', 'sF4', 'pF1', 'pF2', 'pF3', 'pF4', 'oF1',
              'oF2', 'oF3', 'oF4', 'sB1', 'sB2', 'sB3', 'sB4', 'pB1', 'pB2', 'pB3',
              'pB4', 'oB1', 'oB2', 'oB3', 'oB4', 'epoch', 'soe']),
        ]
        for field in fields
    })
    sheets.append(parameters)

parameters = pandas.concat(sheets)
parameters.reset_index(drop=False, inplace=True)
parameters['Filename'] = [filename[:-3] + 'wav' for filename in parameters['Filename']]

/home/herbert/.virtualenvs/stimmenfryslan/lib/python3.5/site-packages/IPython/core/interactiveshell.py:2785: DtypeWarning: Columns (9) have mixed types. Specify dtype option on import or set low_memory=False.
  interactivity=interactivity, compiler=compiler, result=result)


In [16]:
parameters.reset_index(drop=False, inplace=True)

In [29]:
# SELECT user_lat, user_lng, question_text, answer_text
games = pandas.read_sql('''
SELECT language.name as language, item.name as picture,
       survey.user_lat as latitude, survey.user_lng as longitude,
       survey.area_name as area, survey.country_name as country,
       result.recording as filename,
       result.submitted_at as date
FROM       core_surveyresult as survey
INNER JOIN core_picturegameresult as result ON survey.id = result.survey_result_id
INNER JOIN core_language as language ON language.id = result.language_id
INNER JOIN core_picturegameitem as item
    ON result.picture_game_item_id = item.id
''', db)
games['filename'] = [filename.split('/')[-1] for filename in games['filename']]
games = games.set_index('filename')

In [30]:
games_aggregated = games.groupby('filename').aggregate(['first'])

In [27]:
joined = parameters.join(games_aggregated, on='Filename', how='left')

In [31]:
joined

Filename     Energy                 H1A1u             \
                                   mean        std       mean        std   
0       pg_ei_1479_w6ocz.wav   0.006093   0.010032  -8.363866   8.362089   
1        pg_ei_147_jqofa.wav  14.528631  20.464746 -19.329911   7.900788   
2       pg_ei_1490_s2lwa.wav   1.848744   4.192697  15.298327  17.760301   
3       pg_ei_1492_awq4v.wav   1.519375   4.940569  12.590643   6.722463   
4       pg_ei_1498_qo2f4.wav   2.115565   5.390331   3.790873   6.826134   
5       pg_ei_1505_rc6fv.wav   0.485461   1.476672  -2.100762   8.216539   
6        pg_ei_152_vg2ni.wav   0.958645   1.520238  -6.613446  10.624312   
7       pg_ei_1532_z0dsl.wav   3.288982   5.083560  -0.829085   7.790741   
8       pg_ei_1533_hqc0r.wav   1.796025   5.255063   8.457886   9.862231   
9        pg_ei_154_7ba6w.wav   0.399040   0.599270 -15.696802  12.624528   
10      pg_ei_1554_68mr7.wav  10.414797  23.115259  -1.156699  11.868009   
11      pg_ei_1578_l9f7a.wav   3.571768   8.638621   0.396819   6.376619   
12      pg_ei_1579_4k9ry.wav   3.021018   8.622227   9.946554  10.294977   
13      pg_ei_1607_rfmaq.wav   0.336351   1.192991  -2.948125   6.610633   
14      pg_ei_1610_njpag.wav   0.143424   0.282195  -2.152259   7.374509   
15      pg_ei_1618_ovshb.wav   2.558292   6.390083   6.196505   9.946098   
16      pg_ei_1633_o1veb.wav   0.150418   0.776917 -13.997056   9.858770   
17       pg_ei_163_1lsft.wav   6.323439  11.797167 -14.739278   7.655092   
18      pg_ei_1656_uzrp4.wav   8.466685  14.659454  14.374309  17.269044   
19      pg_ei_1684_wy32c.wav   0.096580   0.261895  -5.267619   8.452685   
20      pg_ei_1709_3mapl.wav   0.313399   0.981581   6.973205   5.589335   
21       pg_ei_170_3d7bl.wav   0.818965   1.496516  -1.118491   6.793104   
22      pg_ei_1718_wbk8f.wav   2.195919   6.080640  -5.477264   6.817871   
23      pg_ei_1728_o5nfs.wav   4.632836   8.280038  -2.327510   7.041617   
24      pg_ei_1753_3ydgt.wav   1.924188   3.591438   5.916330  10.088331   
25      pg_ei_1760_1xhdy.wav   1.019632   2.883529  -9.413395   5.949749   
26      pg_ei_1767_ycs6j.wav   1.790412   3.232086  19.764376  11.107679   
27      pg_ei_1771_oxlp4.wav   0.797014   1.865066   9.884880   9.840505   
28      pg_ei_1780_2apos.wav   4.209224  11.736406   0.654883   5.967860   
29      pg_ei_1783_y6j1l.wav   4.176013   7.898707  11.995828  13.005395   
...                      ...        ...        ...        ...        ...   
3604  pg_mond_7558_u5yk7.wav   0.253089   1.129148  13.279675   9.040864   
3605  pg_mond_7562_ueiq8.wav   0.124959   0.390776  -4.764390   7.235432   
3606  pg_mond_7565_x30tw.wav   0.710514   5.168457   4.243849   6.062041   
3607  pg_mond_7574_th70g.wav   0.613170   0.792948   1.457276   4.404910   
3608  pg_mond_7590_eg6fj.wav   0.080419   0.248321  -5.826644   6.359726   
3609  pg_mond_7612_ozhis.wav   0.051657   0.189400   2.032265   6.961066   
3610   pg_mond_764_wnvjl.wav   1.390605   3.227143   0.791462   7.444036   
3611  pg_mond_7660_kt7fn.wav   0.203666   1.082149  13.199955   7.345656   
3612  pg_mond_7688_nghm6.wav   0.944088   3.836126  -8.009504   9.505854   
3613  pg_mond_7704_brjtl.wav   0.952383   3.283208   2.934111   7.591404   
3614   pg_mond_771_m9wd2.wav   0.357439   1.170794   1.444918   7.224172   
3615  pg_mond_7753_ekiz1.wav   0.195193   0.385663   2.590834   5.616180   
3616   pg_mond_779_9lhb4.wav   0.270411   1.443022   4.642808   3.817853   
3617    pg_mond_77_r0mw5.wav  12.615063  14.230695  -2.168674   6.853561   
3618   pg_mond_795_kpn9a.wav   0.164596   0.636454   1.260164   6.633398   
3619    pg_mond_79_k2oby.wav   4.051959   8.274621  -1.949634   7.056929   
3620   pg_mond_851_zgdv6.wav   0.187804   0.440421  -1.327140   7.820476   
3621    pg_mond_85_uw0ck.wav   0.544519   1.318256 -11.131253   7.474641   
3622    pg_mond_86_0jp3y.wav   0.202151   0.347113  -5.096460   7.446010   
3623   pg_mond_888_72kyf.wav   2.144732   5.252261  -2.598460   7.80

In [32]:
expected_files = [
    f.split('/')[-1]
    for f in glob(
        '/media/herbert/Herbert Kruitbos/Data Sets/Stimmen Fryslan 2018-06026/picture_game_recordings_for_voice_sauce/pg_*.wav')
]
# ','.join(f[:-3] + 'mat' for f in set(expected_files) - set(parameters['Filename']))

set(expected_files) - set(parameters['Filename'])

{'pg_ei_2862_lr9qm.wav',
 'pg_maan_6266_a6w93.wav',
 'pg_meeuw_485_2rnjh.wav',
 'pg_meeuw_5945_35eyh.wav',
 'pg_meeuw_999_geulp.wav',
 'pg_molen_6659_7jcf6.wav',
 'pg_mond_2795_dy2ot.wav',
 'pg_mond_2862_8urpy.wav',
 'pg_nagel_1060_gmnzf.wav',
 'pg_nagel_2862_yj61v.wav',
 'pg_uil_1967_jtfcp.wav'}

In [33]:
joined.to_excel('/home/herbert/Stimmen_VoiceSauce_all_2_headers.xls')